
# Level 2 Maze Challenge

## Maze Challenge Rules

For Level 2, the maze is randomly generated every time! You need to create an algorithm that works for any maze. The mazes are always solvable, do not have loops, and have fixed starts and goals.

Here are the rules for the maze challenge:

1.  **Goal:** Navigate the robot from the starting point (🏁) to the goal (🏆) in each maze. The starting point will always be (0,0) and the goal will always be (19,19).
2.  **Movement:** You can only move to adjacent cells (N, S, W, or E) if there is no wall between your current position and the desired cell.
3. **Cherry:** There is a cherry (🍒) in the maze. Collecting the cherry is optional but will give you bonus points.
4.  **Information:** Your `choose_move` method in the `MySolver` class only has access to the current robot's position, the cherry's position, and a dictionary of possible moves from your current location. You do not have a global view of the maze.
5.  **Max Moves:** Your agent has a maximum of 2,000 moves to reach the end of the maze.
6.  **Scoring:**
    *   You start with a base score of **10,000 points**.
    *   Points are then adjusted based on your performance:
        *   **Penalty:** **-100 points** for each unit of Manhattan distance between your final position and the goal (ignoring walls).
        *   **Penalty:** **-10 points** for each move made beyond the shortest possible path to the goal.
        *   **Bonus:** **+500 points** if you collect the cherry.
7.  **Explorer Scoring:** The explorer score encourages the robot to explore as much of the maze as possible while still being efficient in its movement. It is calculated as:
    * **Bonus:** **+10 points** for each unique cell visited.
    * **Penalty:** **-1 point** for each move made.
8.  **Objective:** The goal is to maximize your score over many maze runs. This means finding the goal efficiently and collecting the cherry if it's on a path to the goal that doesn't significantly increase the number of moves.

## Pointers for Solving

Here are some pointers to help you improve your maze solver:

*   **Explore Available Moves:** The `possible_moves` dictionary is crucial. It tells you which directions you can move from your current position.
*   **Avoid Walls:** You cannot move through walls. The `possible_moves` dictionary will only contain valid moves. If you try to move into a wall, it'll count as a move, but your robot won't go anywhere!
*   **Keep Track of Visited Cells:** The provided `self.visited` list is a good starting point. You can use this to implement algorithms that avoid infinite loops or prioritize exploring new paths.
*   **Consider Algorithms:** Common maze-solving algorithms like Depth-First Search (DFS), Breadth-First Search (BFS), or even simple wall-following can be adapted to this problem. Remember you only have local information, so a standard implementation might need modification.
*   **The Cherry:** Think about how you can integrate collecting the cherry into your strategy. Is it always worth going for? How can you determine if it's "on the way"?
*   **Experiment and Iterate:** The `run_solver` function allows you to test your solver on a single maze, and `evaluate_solver` runs it on many mazes to get an average score. Use these tools to experiment with different strategies and see how they perform.
*   **Local Information Only:** This is the key constraint. You cannot "see" the whole maze. Your decision must be based *only* on your current position, the cherry's position, and the available moves from your current position.

Good luck!

---

**🚫 Do Not Modify the Setup Code Block 🚫**

The code below is for setting up and running the maze challenge. You should not need to change it to implement your solver. -> go down to the next block where you see "Your Solver Code Here"

---

In [2]:
# Start from a clean state
# %cd /content
# !rm -rf efr-maze-challenge || true
# !git clone --depth 1 https://github.com/Every-Flavor-Robotics/efr-maze-challenge.git
# %cd efr-maze-challenge

# Install requirements
!pwd
%cd ..
!pwd

!pip install -r requirements.txt

# Add repo to Python path and reload to avoid Colab caching
import sys
import importlib
sys.path.insert(0, "/content/efr-maze-challenge")

import maze_challenge
importlib.reload(maze_challenge)

from typing import Dict, List, Set, Tuple

# Get the reverse of a direction for backtracking
REVERSE_DIRECTION = {
    "N": "S",
    "S": "N",
    "E": "W",
    "W": "E",
}


/home/mverghese/efr-maze-challenge/notebooks
/home/mverghese/efr-maze-challenge
/home/mverghese/efr-maze-challenge


---

## 🤖 Your Solver Code Here 🤖

This is the section where you will implement your maze-solving logic within the `MySolver` class. Modify the `choose_move` method to navigate the robot from the start to the goal.

---

In [3]:
# You can import any additional modules here that you might need
import random
import numpy as np
from matplotlib import pyplot as plt

direction_map = {"N":0,
                 "S":1,
                 "E":2,
                 "W":3,
                 }

# reverse_direction_map = {
#     "NORTH": "SOUTH",
#     "SOUTH": "NORTH",
#     "EAST": "WEST",
#     "WEST": "EAST",
# }

class MazeNode:
  def __init__(self, position):
    self.position = position
    self.neighbors = [None,None,None,None]
  
  def add_neighbor(self,node,direction):
    self.neighbors[direction_map[direction]] = node

def link_nodes(node1, direction, node2):
  node1.add_neighbor(node2, direction)
  node2.add_neighbor(node1, REVERSE_DIRECTION[direction])

def BFS(map, starting_loc, width, height):
  cost_map = np.ones((height,width))*np.inf
  frontier = [starting_loc]
  cost_map[starting_loc] = 0
  while len(frontier) > 0:
    current = frontier.pop(0)
    current_node = map[current]
    for neighbor in current_node.neighbors:
      if neighbor is not None:
        # If its the first time visiting a neighbor
        if cost_map[current] + 1 < cost_map[neighbor.position]:
          cost_map[neighbor.position] = cost_map[current] + 1
          frontier.append(neighbor.position)
  return cost_map

def plan_path(map, start, goal, width, height):
  cost_map = np.ones((height,width))*np.inf
  best_neighbor_map = {}
  frontier = [start]
  cost_map[start] = 0
  while len(frontier) > 0:
    current = frontier.pop(0)
    current_node = map[current]
    for neighbor in current_node.neighbors:
      if neighbor is not None:
        # If its the first time visiting a neighbor
        if cost_map[current] + 1 < cost_map[neighbor.position]:
          cost_map[neighbor.position] = cost_map[current] + 1
          best_neighbor_map[neighbor.position] = current
          frontier.append(neighbor.position)
  
  if cost_map[goal] == np.inf:
    return [], False
  # Reconstruct the path
  path = []
  current = goal
  while current != start:
    path.append(current)
    current = best_neighbor_map[current]
  
  # Reverse the path to get it from start to goal
  path.reverse()
  return path, True
    


class MySolver(maze_challenge.Solver):
    """
    🚀 Your Maze Solver

    This is the main class you'll modify to solve the maze challenge.

    Inherit from `Solver` and implement your maze-solving logic in the `choose_move` method.
    The goal is to navigate from the starting point to the goal using only local information.

    You are given:
      - The current position (row, col) of the agent
      - A dictionary of possible moves: Dict[str, Tuple[int, int]]
        where the keys are directions ("NORTH", "SOUTH", "EAST", "WEST")
        and the values are the coordinates of neighboring cells

    You must:
      - Return one of the available direction keys as a string on each call to `choose_move`

    """

    def __init__(self, width: int, height: int):
        """
        Initialize your solver. You can store any internal state here.

        Args:
            width (int): width of the maze
            height (int): height of the maze
        """
        super().__init__(width, height)

        # You can add any variables your solver might need here
        # Variables you define here can be accessed anywhere in the class

        # For example, here's a list that can be used to store which grid cells
        #    have been visited.

        self.width = width
        self.height = height
        self.visited = np.zeros((height,width))
        self.map = {}
        for i in range(height):
          for j in range(width):
            self.map[(i,j)] = MazeNode((i,j))
        
        self.move_value = -10
        self.exploration_value = 10
        self.cherry_value = 500
        self.distance_penalty = -100
        self.max_moves = 2000
        self.goal_location = (height - 1, width - 1)
        self.exploration_period = .0

        self.distance_map = np.zeros((height, width))
        for i in range(height):
          for j in range(width):
            self.distance_map[i,j] = abs(self.goal_location[0] - i) + abs(self.goal_location[1] - j)

        self.move_counter = 0
        self.move_queue = []

        self.verbose = False
    
    def exploration_weight(self):
      if self.move_counter < self.max_moves * self.exploration_period:
        return 0
      else:
        return (self.move_counter - self.max_moves * self.exploration_period) / (self.max_moves * (1 - self.exploration_period))

    def choose_move(
        self,
        position: Tuple[int, int],
        cherry_position: Tuple[int, int],
        possible_moves: Dict[str, Tuple[int, int]],
    ) -> str:
        """
        Decide the next move given the current position and available directions.

        Args:
            position (Tuple[int, int]): Your current (row, col) in the maze
            possible_moves (Dict[str, Tuple[int, int]]): Valid directions and the
                coordinates they would lead to, e.g. {"N": (3, 2), "E": (4, 3)}

        Returns:
            str: One of the keys in `possible_moves`, e.g. "N", "S", etc.
        """

        # You can do anything with the variables you defined above here, and
        #    they will save between calls of this function.

        # For example, to add the current cell to the list of visited cells,
        #    you can do the following.

        # You need to return one of the possible moves, which is the one
        #    that will be executed
        self.move_counter += 1
        current_node = self.map[position]
        for key in possible_moves.keys():
          link_nodes(current_node, key, self.map[possible_moves[key]])
        self.visited[position] = 1
        
          
        if len(self.move_queue) == 0:
          cost_map = BFS(self.map, position, self.width, self.height)
          value_map = cost_map*self.move_value
          if not self.visited[cherry_position]:
            for i in range(self.height):
              for j in range(self.width):
                cherry_distance = abs(cherry_position[0] - i) + abs(cherry_position[1] - j)
                value_map[i,j] += max(self.cherry_value + cherry_distance * self.move_value, 0)

          
          unexplored_map = (self.visited - 1) * -1
          value_map += unexplored_map * self.exploration_value
          value_map += self.distance_map * self.distance_penalty * self.exploration_weight()
          goal_value = value_map[self.goal_location]
          value_map[np.where(self.visited == 1)] = value_map[np.isfinite(value_map)].min() - 1
          value_map[self.goal_location] = goal_value

          if self.verbose:
            plt.matshow(value_map)
            plt.colorbar()
            plt.show()

          best_value = np.max(value_map)
          best_position = tuple(np.argwhere(value_map == best_value)[0])
          self.move_queue, success = plan_path(self.map, position, best_position, self.width, self.height)
          assert success, "No path found to best position"

        next_position = self.move_queue.pop(0)
        move = ""
        for key in possible_moves.keys():
          if possible_moves[key] == next_position:
            move = key
            break
        if move == "":
          raise ValueError("Next position not found in possible moves")
        return move
          



print("✅ Solver created. Test it down below!")

✅ Solver created. Test it down below!


## Running the Solver and Visualizing Results

The code cells below run your `MySolver` class against a maze and show the results.

*   `maze_challenge.run_solver(MySolver, fast=False)`: This command runs your solver on a single maze.
    *   The `fast=False` flag enables the animation of the robot moving through the maze, allowing you to visualize your solver's path.
    *   If `fast=True` (or the flag is omitted), the animation is skipped, and you'll only see the final result and score.

*   `maze_challenge.evaluate_solver(MySolver)`: This command runs your solver on a set of 5,000 randomly generated mazes and provides an average score, giving you a better idea of its performance across different scenarios.

In [7]:
maze_challenge.run_solver(MySolver, fast=False)

Best position: (np.int64(0), np.int64(1)), Value: 340.0
+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+
| 🏁   🤖                     |              |              |    |         |         |              |
+----+----+----+----+    +----+    +----+----+    +----+----+    +----+    +----+    +    +----+    +
|              |              |                   |         |    |                        |         |
+----+----+    +----+----+    +    +----+    +    +----+    +    +    +----+    +    +    +----+----+
|    |         |    |         |    |         |    |    |              |    |    |    |              |
+    +----+    +    +----+    +    +----+----+    +    +    +    +----+    +----+----+----+----+----+
|         |         |         |         |         |         |    |    |                   |         |
+    +----+----+    +----+    +    +    +----+----+    +----+----+    +    +    +----+    +----+    +
|              |    |       

KeyboardInterrupt: 

In [8]:
maze_challenge.run_solver(MySolver, fast=True)

Best position: (np.int64(0), np.int64(1)), Value: 300.0
+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+
| 🏁   🤖 |              |                   |    |         |                   |              |    |
+    +----+----+    +    +    +----+----+----+    +----+    +----+    +----+----+----+    +    +    +
|                   |         |              |              |         |                   |         |
+    +----+    +    +    +----+----+    +----+    +----+    +    +    +----+----+    +    +----+----+
|    |    |    |    |                                  |    |    |    |              |              |
+----+    +    +    +----+----+----+    +----+    +----+----+----+    +----+----+    +    +----+    +
|              |    |                   |                        |         |         |    |         |
+    +----+    +----+----+----+----+    +----+    +----+    +----+    +----+    +----+----+----+----+
|    |                   |  

In [4]:
maze_challenge.evaluate_solver(MySolver)

🏁 Running Maze Solver for 5000 mazes...


Running Samples: 100%|██████████| 5000/5000 [00:15<00:00, 318.08sample/s]



📊 Average Stats Over 5000 Runs
━━━━━━━━━━━━━━━━━━━━━━━━━━━━━
Visited cells            : 266.95
Num moves                : 480.03
Goal reached             : 1.00
Cherry captured          : 0.95
Score                    : 6253.86
Explorer score           : 2189.44
━━━━━━━━━━━━━━━━━━━━━━━━━━━━━
🕒  Completed in 16.10 seconds
